In [124]:
import warnings
warnings.filterwarnings("ignore")

In [125]:
import pandas as pd

In [126]:
imdb = pd.read_csv('IMDB Dataset.csv')

In [127]:
imdb.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [128]:
imdb.shape

(50000, 2)

In [129]:
from sklearn.model_selection import train_test_split

In [130]:
imdb.review

0        One of the other reviewers has mentioned that ...
1        A wonderful little production. <br /><br />The...
2        I thought this was a wonderful way to spend ti...
3        Basically there's a family where a little boy ...
4        Petter Mattei's "Love in the Time of Money" is...
                               ...                        
49995    I thought this movie did a down right good job...
49996    Bad plot, bad dialogue, bad acting, idiotic di...
49997    I am a Catholic taught in parochial elementary...
49998    I'm going to have to disagree with the previou...
49999    No one expects the Star Trek movies to be high...
Name: review, Length: 50000, dtype: object

In [131]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegressionCV
from sklearn.pipeline import make_pipeline

vec = CountVectorizer()
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review,imdb.sentiment)

Pipeline(steps=[('countvectorizer', CountVectorizer()),
                ('logisticregressioncv', LogisticRegressionCV())])

In [132]:
from sklearn import metrics

def print_report(pipe):
    y_test = imdb.sentiment
    y_pred = pipe.predict(imdb.review)
    report = metrics.classification_report(y_test, y_pred)
    print(report)
    print("accuracy: {:0.3f}".format(metrics.accuracy_score(y_test, y_pred)))

print_report(pipe)


              precision    recall  f1-score   support

    negative       0.96      0.95      0.95     25000
    positive       0.95      0.96      0.95     25000

    accuracy                           0.95     50000
   macro avg       0.95      0.95      0.95     50000
weighted avg       0.95      0.95      0.95     50000

accuracy: 0.951


In [133]:
!pip install eli5

In [134]:
import eli5
eli5.show_weights(clf, top=10) #this result is not meaningful, as weight and feature names are not there

In [135]:
eli5.show_weights(clf,feature_names=vec.get_feature_names(),target_names=set(imdb.sentiment)) 
#make sense

In [136]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment)) # explain local prediction

In [137]:
eli5.show_prediction(clf, imdb.review[123], vec=vec,
                     target_names=set(imdb.sentiment)) # explain local prediction

In [138]:
eli5.show_prediction(clf, imdb.review[100], vec=vec,
                     target_names=set(imdb.sentiment)) # explain local prediction

In [139]:
# the BIAS is the intercept term from the model

In [140]:
# the above approach uses a bag of words vectorizer and a linear classifier

In [141]:
# for other classifiers the feature selection could be harder

In [142]:
# Improvement in Modeling pipeline to make more sense out of text classification

In [143]:
vec = CountVectorizer(stop_words='english')
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)


              precision    recall  f1-score   support

    negative       0.95      0.94      0.95     25000
    positive       0.94      0.95      0.95     25000

    accuracy                           0.95     50000
   macro avg       0.95      0.95      0.95     50000
weighted avg       0.95      0.95      0.95     50000

accuracy: 0.948


In [144]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [145]:
# Model improvement using the TF*IDF Vector

In [146]:
from sklearn.feature_extraction.text import TfidfVectorizer

vec = TfidfVectorizer()
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)

              precision    recall  f1-score   support

    negative       0.96      0.95      0.95     25000
    positive       0.95      0.96      0.95     25000

    accuracy                           0.95     50000
   macro avg       0.95      0.95      0.95     50000
weighted avg       0.95      0.95      0.95     50000

accuracy: 0.954


In [147]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [148]:
# TF*IDF with Stop word removal process

In [149]:
vec = TfidfVectorizer(stop_words='english')
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)

              precision    recall  f1-score   support

    negative       0.96      0.95      0.96     25000
    positive       0.95      0.96      0.96     25000

    accuracy                           0.96     50000
   macro avg       0.96      0.96      0.96     50000
weighted avg       0.96      0.96      0.96     50000

accuracy: 0.956


In [150]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [151]:
# N-gram based on words vs. N-Gram based on characters of words, which one is better

In [152]:
vec = TfidfVectorizer(stop_words='english', analyzer='char',
                      ngram_range=(2,5))
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)

              precision    recall  f1-score   support

    negative       1.00      1.00      1.00     25000
    positive       1.00      1.00      1.00     25000

    accuracy                           1.00     50000
   macro avg       1.00      1.00      1.00     50000
weighted avg       1.00      1.00      1.00     50000

accuracy: 0.998


In [153]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [154]:
# char analyzer creates character n-grams but it takes a lot of time
# char_wb analyzer creates character n-grams, but those characters does not cross word boundaries 

In [155]:
vec = TfidfVectorizer(stop_words='english', analyzer='char_wb',
                      ngram_range=(2,5))
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)

              precision    recall  f1-score   support

    negative       0.99      0.99      0.99     25000
    positive       0.99      0.99      0.99     25000

    accuracy                           0.99     50000
   macro avg       0.99      0.99      0.99     50000
weighted avg       0.99      0.99      0.99     50000

accuracy: 0.989


In [156]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [157]:
# to deal with large vocabularies we can use Hashing vectorizer instead of count or tfidf vectorizer
# this time we need a complex algorithm to classify, instead of simple linear model

In [159]:
from sklearn.feature_extraction.text import HashingVectorizer
from sklearn.linear_model import SGDClassifier

vec = HashingVectorizer(stop_words='english', ngram_range=(1,2))
clf = SGDClassifier(random_state=42)
pipe = make_pipeline(vec, clf)
pipe.fit(imdb.review, imdb.sentiment)

print_report(pipe)

              precision    recall  f1-score   support

    negative       0.92      0.90      0.91     25000
    positive       0.90      0.92      0.91     25000

    accuracy                           0.91     50000
   macro avg       0.91      0.91      0.91     50000
weighted avg       0.91      0.91      0.91     50000

accuracy: 0.909


In [160]:
eli5.show_prediction(clf, imdb.review[0], vec=vec,
                     target_names=set(imdb.sentiment),
                     targets=['positive'])

In [161]:
# InvertableHashingVectorizer. It can be used to get feature names for HahshingVectorizer 
# without fitiing a huge vocabulary

In [162]:
from eli5.sklearn import InvertableHashingVectorizer
import numpy as np

In [163]:
ivec = InvertableHashingVectorizer(vec)
sample_size = len(imdb.review) // 10
X_sample = np.random.choice(imdb.review, size=sample_size)
ivec.fit(X_sample)

InvertableHashingVectorizer(vec=HashingVectorizer(ngram_range=(1, 2),
                                                  stop_words='english'))

In [164]:
eli5.show_weights(clf, vec=ivec, top=20,
                  target_names=set(imdb.sentiment))

If a library is not supported by eli5 directly, or the text processing pipeline is too complex for eli5, eli5 can still help - it provides an implementation of LIME (Ribeiro et al., 2016) algorithm which allows to explain predictions of arbitrary classifiers, including text classifiers. eli5.lime can also help when it is hard to get exact mapping between model coefficients and text features, e.g. if there is dimension reduction involved.

In [165]:
import pandas as pd
df = pd.read_csv('complaints.csv')
df.shape
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1989953 entries, 0 to 1989952
Data columns (total 18 columns):
 #   Column                        Dtype 
---  ------                        ----- 
 0   Date received                 object
 1   Product                       object
 2   Sub-product                   object
 3   Issue                         object
 4   Sub-issue                     object
 5   Consumer complaint narrative  object
 6   Company public response       object
 7   Company                       object
 8   State                         object
 9   ZIP code                      object
 10  Tags                          object
 11  Consumer consent provided?    object
 12  Submitted via                 object
 13  Date sent to company          object
 14  Company response to consumer  object
 15  Timely response?              object
 16  Consumer disputed?            object
 17  Complaint ID                  int64 
dtypes: int64(1), object(17)
memory usage: 273.

In [166]:
# Create a new dataframe with two columns
df1 = df[['Product', 'Consumer complaint narrative']].copy()


In [167]:
# Remove missing values (NaN)
df1 = df1[pd.notnull(df1['Consumer complaint narrative'])]


In [168]:
# Renaming second column for a simpler name
df1.columns = ['Product', 'Consumer_complaint'] 


In [169]:
df1.shape


(675946, 2)

In [170]:
# Because the computation is time consuming (in terms of CPU), the data was sampled
df2 = df1.sample(20000, random_state=1).copy()


In [171]:
# Renaming categories
df2.replace({'Product': 
             {'Credit reporting, credit repair services, or other personal consumer reports': 
              'Credit reporting, repair, or other', 
              'Credit reporting': 'Credit reporting, repair, or other',
             'Credit card': 'Credit card or prepaid card',
             'Prepaid card': 'Credit card or prepaid card',
             'Payday loan': 'Payday loan, title loan, or personal loan',
             'Money transfer': 'Money transfer, virtual currency, or money service',
             'Virtual currency': 'Money transfer, virtual currency, or money service'}}, 
            inplace= True)


In [172]:
df2.head()

Product  \
868190                                           Mortgage   
34778                                        Student loan   
752231  Money transfer, virtual currency, or money ser...   
715237                 Credit reporting, repair, or other   
171294                 Credit reporting, repair, or other   

                                       Consumer_complaint  
868190  Dear CFPB, I currently have a Bank of America ...  
34778   XXXX XXXX XXXX XXXX XXXX XXXX. # XXXX XXXX Oh ...  
752231  Here is a brief timeline of events that I can ...  
715237  I sent a total of 5 letter to TransUnion regar...  
171294  I checked my credit using XXXX on XX/XX/XXXX a...

In [173]:
pd.DataFrame(df2.Product.unique())


0
0                                            Mortgage
1                                        Student loan
2   Money transfer, virtual currency, or money ser...
3                  Credit reporting, repair, or other
4                                     Debt collection
5                         Credit card or prepaid card
6                         Checking or savings account
7                                       Consumer Loan
8                               Vehicle loan or lease
9           Payday loan, title loan, or personal loan
10                            Bank account or service
11                                    Money transfers
12                            Other financial service

In [174]:
# Create a new column 'category_id' with encoded categories 
df2['category_id'] = df2['Product'].factorize()[0]
category_id_df = df2[['Product', 'category_id']].drop_duplicates()


In [175]:
# Dictionaries for future use
category_to_id = dict(category_id_df.values)
id_to_category = dict(category_id_df[['category_id', 'Product']].values)


In [176]:
# New dataframe
df2.head()


Product  \
868190                                           Mortgage   
34778                                        Student loan   
752231  Money transfer, virtual currency, or money ser...   
715237                 Credit reporting, repair, or other   
171294                 Credit reporting, repair, or other   

                                       Consumer_complaint  category_id  
868190  Dear CFPB, I currently have a Bank of America ...            0  
34778   XXXX XXXX XXXX XXXX XXXX XXXX. # XXXX XXXX Oh ...            1  
752231  Here is a brief timeline of events that I can ...            2  
715237  I sent a total of 5 letter to TransUnion regar...            3  
171294  I checked my credit using XXXX on XX/XX/XXXX a...            3

In [184]:
df2.Product.value_counts()

Credit reporting, repair, or other                    8231
Debt collection                                       4075
Mortgage                                              2216
Credit card or prepaid card                           2000
Checking or savings account                            849
Student loan                                           788
Bank account or service                                441
Vehicle loan or lease                                  374
Money transfer, virtual currency, or money service     358
Payday loan, title loan, or personal loan              312
Consumer Loan                                          296
Money transfers                                         53
Other financial service                                  7
Name: Product, dtype: int64

In [185]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.linear_model import LogisticRegressionCV
from sklearn.pipeline import make_pipeline

vec = CountVectorizer()
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint,df2.Product)

Pipeline(steps=[('countvectorizer', CountVectorizer()),
                ('logisticregressioncv', LogisticRegressionCV())])

In [186]:
from sklearn import metrics

def print_report(pipe):
    y_test = df2.Product
    y_pred = pipe.predict(df2.Consumer_complaint)
    report = metrics.classification_report(y_test, y_pred)
    print(report)
    print("accuracy: {:0.3f}".format(metrics.accuracy_score(y_test, y_pred)))

print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.97      0.74      0.84       441
                       Checking or savings account       0.91      0.87      0.89       849
                                     Consumer Loan       0.98      0.59      0.74       296
                       Credit card or prepaid card       0.91      0.85      0.88      2000
                Credit reporting, repair, or other       0.87      0.95      0.91      8231
                                   Debt collection       0.87      0.85      0.86      4075
Money transfer, virtual currency, or money service       0.92      0.80      0.86       358
                                   Money transfers       1.00      0.70      0.82        53
                                          Mortgage       0.96      0.95      0.95      2216
                           Other financial service       1.00      0.57      0.

In [187]:
import eli5
eli5.show_weights(clf, top=10) 
#this result is not meaningful, as weight and feature names are not there


In [190]:
eli5.show_weights(clf,feature_names=vec.get_feature_names(),target_names=set(df2.Product)) 
#make sense


In [197]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product)) # explain local prediction


In [196]:
np.array(df2.Consumer_complaint)[0]

'Dear CFPB, I currently have a Bank of America mortgage and am unable to contact " customer service \'\' for any assistance on my loan or impound account. On XXXX XXXX, XXXX, I was " on hold \'\' XXXX hours trying to reach a representative to ask a simple question about my impound account and finally got disconnected from their phone bank. \nTHIS IS UNACCEPTABLE. I am calling about my home. I am a customer. The use of a so called " customer service \'\' number by Bank of America is hypocrisy because what is going on is instead customer ABUSE. \nWhy should I have to wait XXXX hours during my work week to try to speak with a representative about my home mortgage? They should be required to have a call back service or something that does not hold customers XXXX for hours to their negligence, disregard and abuse of customers. \nPlease advise what you plan to do about this. \nSincerely, Customer'

In [198]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[123], vec=vec,
                     target_names=set(df2.Product)) # explain local prediction


In [199]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[100], vec=vec,
                     target_names=set(df2.Product)) # explain local prediction


In [200]:
vec = CountVectorizer(stop_words='english')
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)

print_report(pipe)

                                                    precision    recall  f1-score   support

                           Bank account or service       0.95      0.71      0.81       441
                       Checking or savings account       0.90      0.85      0.87       849
                                     Consumer Loan       0.96      0.52      0.68       296
                       Credit card or prepaid card       0.89      0.84      0.86      2000
                Credit reporting, repair, or other       0.86      0.95      0.90      8231
                                   Debt collection       0.86      0.84      0.85      4075
Money transfer, virtual currency, or money service       0.92      0.80      0.85       358
                                   Money transfers       0.97      0.62      0.76        53
                                          Mortgage       0.95      0.94      0.95      2216
                           Other financial service       1.00      0.43      0.

In [201]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))


In [202]:
from sklearn.feature_extraction.text import TfidfVectorizer

vec = TfidfVectorizer()
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)
print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.95      0.73      0.82       441
                       Checking or savings account       0.86      0.90      0.88       849
                                     Consumer Loan       0.92      0.53      0.68       296
                       Credit card or prepaid card       0.88      0.89      0.89      2000
                Credit reporting, repair, or other       0.91      0.94      0.92      8231
                                   Debt collection       0.88      0.88      0.88      4075
Money transfer, virtual currency, or money service       0.88      0.83      0.86       358
                                   Money transfers       0.96      0.49      0.65        53
                                          Mortgage       0.93      0.97      0.95      2216
                           Other financial service       0.00      0.00      0.

In [203]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))


In [204]:
vec = TfidfVectorizer(stop_words='english')
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)
print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.93      0.76      0.83       441
                       Checking or savings account       0.87      0.90      0.88       849
                                     Consumer Loan       0.94      0.60      0.74       296
                       Credit card or prepaid card       0.88      0.90      0.89      2000
                Credit reporting, repair, or other       0.91      0.94      0.93      8231
                                   Debt collection       0.89      0.88      0.89      4075
Money transfer, virtual currency, or money service       0.89      0.85      0.87       358
                                   Money transfers       0.96      0.49      0.65        53
                                          Mortgage       0.94      0.97      0.96      2216
                           Other financial service       0.00      0.00      0.

In [205]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))


In [206]:
vec = TfidfVectorizer(stop_words='english', analyzer='char',
                      ngram_range=(2,5))
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)

print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.95      0.75      0.84       441
                       Checking or savings account       0.88      0.91      0.90       849
                                     Consumer Loan       0.98      0.56      0.71       296
                       Credit card or prepaid card       0.89      0.91      0.90      2000
                Credit reporting, repair, or other       0.92      0.95      0.94      8231
                                   Debt collection       0.89      0.90      0.90      4075
Money transfer, virtual currency, or money service       0.90      0.85      0.87       358
                                   Money transfers       1.00      0.38      0.55        53
                                          Mortgage       0.94      0.97      0.95      2216
                           Other financial service       0.00      0.00      0.

In [207]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))


In [208]:
vec = TfidfVectorizer(stop_words='english', analyzer='char_wb',
                      ngram_range=(2,5))
clf = LogisticRegressionCV()
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)

print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.92      0.63      0.75       441
                       Checking or savings account       0.82      0.87      0.84       849
                                     Consumer Loan       0.94      0.49      0.64       296
                       Credit card or prepaid card       0.85      0.88      0.87      2000
                Credit reporting, repair, or other       0.90      0.93      0.92      8231
                                   Debt collection       0.86      0.87      0.86      4075
Money transfer, virtual currency, or money service       0.86      0.80      0.83       358
                                   Money transfers       1.00      0.32      0.49        53
                                          Mortgage       0.92      0.96      0.94      2216
                           Other financial service       0.00      0.00      0.

In [209]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))

In [211]:
from sklearn.feature_extraction.text import HashingVectorizer
from sklearn.linear_model import SGDClassifier

vec = HashingVectorizer(stop_words='english', ngram_range=(1,2))
clf = SGDClassifier(random_state=42)
pipe = make_pipeline(vec, clf)
pipe.fit(df2.Consumer_complaint, df2.Product)
print_report(pipe)


                                                    precision    recall  f1-score   support

                           Bank account or service       0.97      0.47      0.63       441
                       Checking or savings account       0.77      0.79      0.78       849
                                     Consumer Loan       0.98      0.49      0.66       296
                       Credit card or prepaid card       0.82      0.83      0.83      2000
                Credit reporting, repair, or other       0.86      0.93      0.89      8231
                                   Debt collection       0.86      0.82      0.84      4075
Money transfer, virtual currency, or money service       0.91      0.73      0.81       358
                                   Money transfers       1.00      0.68      0.81        53
                                          Mortgage       0.86      0.96      0.91      2216
                           Other financial service       0.50      0.14      0.

In [212]:
eli5.show_prediction(clf, np.array(df2.Consumer_complaint)[0], vec=vec,
                     target_names=set(df2.Product))

In [213]:
from eli5.sklearn import InvertableHashingVectorizer
import numpy as np

ivec = InvertableHashingVectorizer(vec)
sample_size = len(df2.Consumer_complaint) // 10
X_sample = np.random.choice(df2.Consumer_complaint, size=sample_size)
ivec.fit(X_sample)

eli5.show_weights(clf, vec=ivec, top=20,
                  target_names=set(df2.Product))